# Choropleth map 

In [867]:
import pandas as pd
import duckdb 

df = pd.read_excel("data/resultat-ansokningsomgang-2024.xlsx", sheet_name= "Tabell 3", skiprows=5)

df.head()

Utbildningsområde SUN5 inriktning                   SUN5 inriktning namn  \
0           Data/IT           481ab  Utbildningar till programmerare, spel   
1           Data/IT           481ab  Utbildningar till programmerare, spel   
2           Data/IT           481ab  Utbildningar till programmerare, spel   
3           Data/IT           481ab  Utbildningar till programmerare, spel   
4           Data/IT           481ab  Utbildningar till programmerare, spel   

                                Utbildningsnamn    Beslut   Diarienummer  \
0                                 AI Programmer    Avslag  MYH 2024/3742   
1  Forsbergs, Spelutvecklare – Game Programming    Avslag  MYH 2024/4174   
2    Futuregames Game Programmer Specialization    Avslag  MYH 2024/3029   
3                               Game Programmer    Avslag  MYH 2024/3425   
4                             Spelprogrammerare  Beviljad  MYH 2024/3852   

  Flera kommuner  Antal kommuner             Län          Kommun  ...  \
0            Nej               1    Västerbotten            Umeå  ...   
1            Nej               1       Stockholm       Stockholm  ...   
2             Ja               2  Flera kommuner  Flera kommuner  ...   
3            Nej               1        Blekinge       Karlshamn  ...   
4            Nej               1           Skåne           Malmö  ...   

   Sökta utbildningsomgångar Beviljade utbildningsomgångar  \
0                          3                             0   
1                          3                             0   
2                          3                             0   
3                          3                             0   
4                          4                             3   

   Sökta platser per utbildningsomgång Sökta platser totalt  \
0                                   30                   90   
1                                   20                   60   
2                                   30                   90   
3                                   25                   75   
4                                   35                  140   

   Beviljade platser utbildningsomgång 1  \
0                                      0   
1                                      0   
2                                      0   
3                                      0   
4                                     35   

  Beviljade platser utbildningsomgång 2 Beviljade platser utbildningsomgång 3  \
0                                     0                                     0   
1                                     0                                     0   
2                                     0                                     0   
3                                     0                                     0   
4                                    35                                    35   

  Beviljade platser utbildningsomgång 4  \
0                                     0   
1                                     0   
2                                     0   
3                                     0   
4                                     0   

   Beviljade platser utbildningsomgång 5  Beviljade platser totalt  
0                                      0                         0  
1                                      0                         0  
2                                      0                         0  
3                                      0                         0  
4                                      0                       105  

[5 rows x 28 columns]

In [868]:
decisions = df["Beslut"].value_counts()
approved, total = decisions["Beviljad"], decisions.sum()
approved, total

(np.int64(344), np.int64(1272))

In [869]:
df_regions =duckdb.query(
    """--sql
    SELECT
        län,
        CASt(COUNT_IF(beslut= 'Beviljad') as INTEGER) AS Beviljade
    FROM 
        df 
    WHERE 
        län != 'Flera kommuner'
    GROUP BY 
        län
    ORDER BY 
        beviljade
    DESC, län ASC;
    """
).df()

df_regions

Län  Beviljade
0         Stockholm         82
1   Västra Götaland         63
2             Skåne         37
3      Östergötland         16
4         Jönköping         13
5            Örebro         10
6    Västernorrland          6
7         Gävleborg          5
8            Kalmar          5
9         Kronoberg          5
10      Västmanland          5
11          Dalarna          4
12          Halland          4
13       Norrbotten          4
14          Uppsala          4
15         Värmland          4
16     Västerbotten          4
17         Blekinge          3
18     Södermanland          3
19         Jämtland          2

In [870]:
type(df_regions)

pandas.core.frame.DataFrame

In [871]:
df_regions["Län"].values

array(['Stockholm', 'Västra Götaland', 'Skåne', 'Östergötland',
       'Jönköping', 'Örebro', 'Västernorrland', 'Gävleborg', 'Kalmar',
       'Kronoberg', 'Västmanland', 'Dalarna', 'Halland', 'Norrbotten',
       'Uppsala', 'Värmland', 'Västerbotten', 'Blekinge', 'Södermanland',
       'Jämtland'], dtype=object)

In [872]:
import json
with open("assets/swedish_regions.geojson", "r", encoding= "utf-8") as file:
    json_data = json.load(file)
    
json_data.get("features")[0].get("properties")

{'admin_level': '4',
 'boundary': 'administrative',
 'name': 'Gotlands län',
 'ref:se:län:bokstav': 'I',
 'ref:se:länskod': '09',
 'type': 'multipolygon'}

In [873]:
properties = [feature.get("properties") for feature in json_data.get("features")]
region_codes = {property.get("name"): property.get("ref:se:länskod") for property in properties}

region_codes

{'Gotlands län': '09',
 'Kalmar län': '08',
 'Blekinge län': '10',
 'Jämtlands län': '23',
 'Västerbottens län': '24',
 'Kronobergs län': '07',
 'Västra Götalands län': '14',
 'Värmlands län': '17',
 'Dalarnas län': '20',
 'Södermanlands län': '04',
 'Jönköpings län': '06',
 'Östergötlands län': '05',
 'Stockholms län': '01',
 'Västmanlands län': '19',
 'Uppsala län': '03',
 'Gävleborgs län': '21',
 'Västernorrlands län': '22',
 'Örebro län': '18',
 'Norrbottens län': '25',
 'Hallands län': '13',
 'Skåne län': '12'}

In [874]:
from difflib import get_close_matches

get_close_matches("appel", ["ape", "apple", "peach", "puppy"])
['apple', 'ape']

['apple', 'ape']

In [875]:
get_close_matches("appel", ["ape", "apple", "peach", "puppy"])
['apple', 'ape'][0]

'apple'

In [876]:
df_regions["Län"].iloc[0]

'Stockholm'

In [877]:
region = get_close_matches(df_regions["Län"].iloc[0], region_codes.keys())[0]
region

'Stockholms län'

In [878]:
region_codes[region]

'01'

In [879]:
region_codes_map = []
for region in df_regions["Län"]:
    region_name = get_close_matches(region, region_codes.keys(), n= 1)[0]
    code = region_codes[region_name]
    region_codes_map.append(code)
    
region_codes_map

['01',
 '14',
 '12',
 '05',
 '06',
 '18',
 '22',
 '21',
 '08',
 '07',
 '19',
 '20',
 '13',
 '25',
 '03',
 '17',
 '24',
 '10',
 '04',
 '23']

In [880]:
print(region_codes_map)
print(df_regions["Län"].values)

['01', '14', '12', '05', '06', '18', '22', '21', '08', '07', '19', '20', '13', '25', '03', '17', '24', '10', '04', '23']
['Stockholm' 'Västra Götaland' 'Skåne' 'Östergötland' 'Jönköping' 'Örebro'
 'Västernorrland' 'Gävleborg' 'Kalmar' 'Kronoberg' 'Västmanland' 'Dalarna'
 'Halland' 'Norrbotten' 'Uppsala' 'Värmland' 'Västerbotten' 'Blekinge'
 'Södermanland' 'Jämtland']


In [881]:
import numpy as np


log_approved = np.log(df_regions["Beviljade"] + 1)


## Draw map

In [882]:
import plotly.graph_objects as go
import numpy as np


log_approved = np.log(df_regions["Beviljade"] + 1)

fig = go.Figure(
    go.Choroplethmapbox(
        geojson = json_data,
        locations= region_codes_map,
        z = log_approved,
        featureidkey= "properties.ref:se:länskod",
        colorscale="Blues",
        showscale=False,
        customdata=df_regions["Beviljade"],
        text= df_regions["Län"],
        hovertemplate="<b>%{text}</b><br>Beviljade utbildningar %{customdata}<extra></extra>",
        marker_line_width= 0.3),
        
)


fig.update_layout(
    mapbox= dict(style= "white-bg", zoom= 3.3, center= dict(lat=62.6952, lon= 13.9149)),
    width= 470,
    height= 500,
    margin= dict(r=0, t=50, l=0, b=0),
    title=dict(
        text=f"""
                <b>Antal beviljade</b>
                <br>utbildningar per län
                <br>inom YH i Sverige för 
                <br>omgång 2024. Ju mörkare 
                <br>blå färg, desto fler
                <br>beviljade utbildningar
                <br>
                <br><b>{approved}</b> av totalt <b>{total}</b>
                <br>ansökningar har
                <br>godkänts, vilket innebär 
                <br><b>{approved/total * 100:.0f}%</b> beviljandegrad
                <br>
                <br><b>I ledningen är</b>
                <br>1. Stockholm, 
                <br>2. Västra Götaland
                <br>3. Skåne""",
            x=0.06,
            y= 0.75,
            font=dict(size=13)
    )
)


fig.show()

C:\Users\Marcus\AppData\Local\Temp\ipykernel_6776\250412453.py:8: DeprecationWarning:

*choroplethmapbox* is deprecated! Use *choroplethmap* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/



## Exercise for reader
1. filter on different education areas
2. approved educations on municipality level

In [883]:
df

Utbildningsområde SUN5 inriktning  \
0               Data/IT           481ab   
1               Data/IT           481ab   
2               Data/IT           481ab   
3               Data/IT           481ab   
4               Data/IT           481ab   
...                 ...             ...   
1267  Transporttjänster           840da   
1268  Transporttjänster           840da   
1269  Transporttjänster           840dy   
1270             Övrigt           999za   
1271             Övrigt           999za   

                       SUN5 inriktning namn  \
0     Utbildningar till programmerare, spel   
1     Utbildningar till programmerare, spel   
2     Utbildningar till programmerare, spel   
3     Utbildningar till programmerare, spel   
4     Utbildningar till programmerare, spel   
...                                     ...   
1267        Utbildningar till trafikflygare   
1268        Utbildningar till trafikflygare   
1269           Övriga utbildningar luftfart   
1270  Traditionella hantverksyrken, lärling   
1271  Traditionella hantverksyrken, lärling   

                                        Utbildningsnamn    Beslut  \
0                                         AI Programmer    Avslag   
1          Forsbergs, Spelutvecklare – Game Programming    Avslag   
2            Futuregames Game Programmer Specialization    Avslag   
3                                       Game Programmer    Avslag   
4                                     Spelprogrammerare  Beviljad   
...                                                 ...       ...   
1267        Integrerad Trafikflygarutbildning Statsstöd    Avslag   
1268  Trafikflygare med inriktning hållbarhet och pi...    Avslag   
1269                  UAS-operatör inom Samhällsbyggnad    Avslag   
1270  Hantverkslärling - smala och traditionella han...  Beviljad   
1271     Lärlingsutbildning inom traditionellt hantverk  Beviljad   

       Diarienummer Flera kommuner  Antal kommuner              Län  \
0     MYH 2024/3742            Nej               1     Västerbotten   
1     MYH 2024/4174            Nej               1        Stockholm   
2     MYH 2024/3029             Ja               2   Flera kommuner   
3     MYH 2024/3425            Nej               1         Blekinge   
4     MYH 2024/3852            Nej               1            Skåne   
...             ...            ...             ...              ...   
1267  MYH 2024/3675            Nej               1  Västra Götaland   
1268  MYH 2024/3415            Nej               1     Västerbotten   
1269  MYH 2024/3326             Ja               5   Flera kommuner   
1270  MYH 2024/3586            Nej               1          Dalarna   
1271  MYH 2024/3026            Nej               1        Stockholm   

              Kommun  ...  Sökta utbildningsomgångar  \
0               Umeå  ...                          3   
1          Stockholm  ...                          3   
2     Flera kommuner  ...                          3   
3          Karlshamn  ...                          3   
4              Malmö  ...                          4   
...              ...  ...                        ...   
1267        Göteborg  ...                          5   
1268      Skellefteå  ...                          5   
1269  Flera kommuner  ...                          3   
1270         Leksand  ...                          5   
1271       Stockholm  ...                          5   

     Beviljade utbildningsomgångar  Sökta platser per utbildningsomgång  \
0                                0                                   30   
1                                0                                   20   
2                                0                                   30   
3                                0                                   25   
4                                3                                   35   
...                            ...                                  ...   
1267                             0          

In [884]:

df[(df["Beslut"] == "Beviljad") & (df["Län"] == "Stockholm")]["Utbildningsområde"].value_counts()

Utbildningsområde
Ekonomi, administration och försäljning         18
Samhällsbyggnad och byggteknik                  17
Data/IT                                         15
Hälso- och sjukvård samt socialt arbete          7
Teknik och tillverkning                          7
Kultur, media och design                         6
Transporttjänster                                3
Säkerhetstjänster                                2
Hotell, restaurang och turism                    2
Friskvård och kroppsvård                         1
Juridik                                          1
Lantbruk, djurvård, trädgård, skog och fiske     1
Pedagogik och undervisning                       1
Övrigt                                           1
Name: count, dtype: int64

In [885]:
df_education_areas = df[df["Beslut"] == "Beviljad"][["Utbildningsområde", "Kommun"]].value_counts()


In [886]:
df_education_areas = df_education_areas.reset_index()

In [887]:
df_education_areas.rename(columns={"count": "Antal beviljade"}, inplace=True)

In [888]:
df_education_areas

Utbildningsområde          Kommun  Antal beviljade
0                    Teknik och tillverkning  Flera kommuner               18
1    Ekonomi, administration och försäljning       Stockholm               18
2             Samhällsbyggnad och byggteknik  Flera kommuner               14
3             Samhällsbyggnad och byggteknik       Stockholm               12
4                                    Data/IT       Stockholm               11
..                                       ...             ...              ...
143                  Teknik och tillverkning    Örnsköldsvik                1
144                        Transporttjänster           Malmö                1
145                        Transporttjänster       Stockholm                1
146                                   Övrigt         Leksand                1
147                                   Övrigt       Stockholm                1

[148 rows x 3 columns]

In [889]:

with open("assets/swedish_municipalities.geojson", "r", encoding= "utf-8") as file:
    json_data_municipality= json.load(file) 
    
json_data_municipality

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'geometry': {'type': 'Polygon',
    'coordinates': [[[18.468388530752513, 59.21953012697554],
      [18.418237381066064, 59.24139741653453],
      [18.38900706518804, 59.263493577275504],
      [18.385013581949266, 59.231470171058746],
      [18.332235016239352, 59.249973658086276],
      [18.28010505679042, 59.26291395523028],
      [18.2662858149297, 59.2570487744373],
      [18.200077544069796, 59.24747266544313],
      [18.177187170681023, 59.23242651177156],
      [18.18313986536157, 59.21083179106294],
      [18.20163522538779, 59.20864188178615],
      [18.24315341186918, 59.217748022392776],
      [18.250450609370876, 59.209490824196024],
      [18.305017778414083, 59.18314755272288],
      [18.333661262455102, 59.15842526668708],
      [18.405759428968686, 59.16909793135661],
      [18.42590589007953, 59.18504063853134],
      [18.42341062927856, 59.202756937946084],
      [18.437234525867147, 59.21379800878891

In [890]:
json_data_municipality["features"][0]["properties"]["kom_namn"]

'Tyresö'

In [891]:
json_data_municipality

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'geometry': {'type': 'Polygon',
    'coordinates': [[[18.468388530752513, 59.21953012697554],
      [18.418237381066064, 59.24139741653453],
      [18.38900706518804, 59.263493577275504],
      [18.385013581949266, 59.231470171058746],
      [18.332235016239352, 59.249973658086276],
      [18.28010505679042, 59.26291395523028],
      [18.2662858149297, 59.2570487744373],
      [18.200077544069796, 59.24747266544313],
      [18.177187170681023, 59.23242651177156],
      [18.18313986536157, 59.21083179106294],
      [18.20163522538779, 59.20864188178615],
      [18.24315341186918, 59.217748022392776],
      [18.250450609370876, 59.209490824196024],
      [18.305017778414083, 59.18314755272288],
      [18.333661262455102, 59.15842526668708],
      [18.405759428968686, 59.16909793135661],
      [18.42590589007953, 59.18504063853134],
      [18.42341062927856, 59.202756937946084],
      [18.437234525867147, 59.21379800878891

In [892]:
properties_municipality = [feature.get("properties") for feature in json_data_municipality.get("features")]
municipality_codes= {property.get("kom_namn"): property.get("id") for property in properties_municipality} 
municipality_codes


{'Tyresö': '0138',
 'Södertälje': '0181',
 'Östhammar': '0382',
 'Gnesta': '0461',
 'Hultsfred': '0860',
 'Borås': '1490',
 'Borlänge': '2081',
 'Storuman': '2421',
 'Boden': '2582',
 'Solna': '0184',
 'Strömstad': '1486',
 'Tidaholm': '1498',
 'Forshaga': '1763',
 'Ludvika': '2085',
 'Örnsköldsvik': '2284',
 'Gällivare': '2523',
 'Norrtälje': '0188',
 'Sigtuna': '0191',
 'Nynäshamn': '0192',
 'Varberg': '1383',
 'Krokom': '2309',
 'Danderyd': '0162',
 'Finspång': '0562',
 'Alvesta': '0764',
 'Älmhult': '0765',
 'Karlskrona': '1080',
 'Ängelholm': '1292',
 'Kungsbacka': '1384',
 'Skövde': '1496',
 'Storfors': '1760',
 'Mora': '2062',
 'Järfälla': '0123',
 'Nyköping': '0480',
 'Växjö': '0780',
 'Högsby': '0821',
 'Åstorp': '1277',
 'Sotenäs': '1427',
 'Mellerud': '1461',
 'Hallsberg': '1861',
 'Ånge': '2260',
 'Kramfors': '2282',
 'Överkalix': '2513',
 'Luleå': '2580',
 'Uppvidinge': '0760',
 'Mönsterås': '0861',
 'Burlöv': '1231',
 'Örkelljunga': '1257',
 'Alingsås': '1489',
 'Torsby':

In [893]:
data_it = df_education_areas[
    (df_education_areas["Utbildningsområde"] == "Data/IT")
    & (df_education_areas["Kommun"] != "Flera kommuner")
]
data_it

Utbildningsområde       Kommun  Antal beviljade
4            Data/IT    Stockholm               11
12           Data/IT     Göteborg                6
13           Data/IT        Malmö                6
18           Data/IT        Solna                4
30           Data/IT      Mölndal                2
57           Data/IT      Värnamo                1
58           Data/IT        Växjö                1
59           Data/IT       Örebro                1
60           Data/IT        Borås                1
61           Data/IT    Jönköping                1
64           Data/IT  Trollhättan                1

In [894]:
municipality= get_close_matches(data_it["Kommun"].iloc[0], municipality_codes.keys())[0]
municipality_codes[municipality]


'0180'

In [895]:
municipality_codes_map = []
for municipality in data_it["Kommun"]:
    municipality_name =  get_close_matches(municipality, municipality_codes.keys(), n=1)[0]
        
    code = municipality_codes[municipality_name]

    municipality_codes_map.append(code)
    
    
municipality_codes_map   


['0180',
 '1480',
 '1280',
 '0184',
 '1481',
 '0683',
 '0780',
 '1880',
 '1490',
 '0680',
 '1488']

In [896]:
print(municipality_codes_map)
print(data_it["Kommun"].values)

['0180', '1480', '1280', '0184', '1481', '0683', '0780', '1880', '1490', '0680', '1488']
['Stockholm' 'Göteborg' 'Malmö' 'Solna' 'Mölndal' 'Värnamo' 'Växjö'
 'Örebro' 'Borås' 'Jönköping' 'Trollhättan']


In [897]:
municipality_codes_map

['0180',
 '1480',
 '1280',
 '0184',
 '1481',
 '0683',
 '0780',
 '1880',
 '1490',
 '0680',
 '1488']

In [ ]:

# create a dataframe thats pick out all the name on the municipality and the unique id from municipality_codes (is a dictionary)
df_geo_municipalities = pd.DataFrame({
    "Kommun": namn,
    "Geo_id": id}
    for namn, id in municipality_codes.items()
)

In [ ]:

# Merge df_geo_muncipalities with data_it too get all coordinates to municipality and fillout the one who's have zero approved
data__it_fillout = df_geo_municipalities.merge(
    data_it[["Kommun", "Antal beviljade"]],
    on= "Kommun",
    how= "left"
)

data__it_fillout["Antal beviljade"] = data__it_fillout["Antal beviljade"].fillna(0)

In [900]:
data_it_approved = np.log(data__it_fillout["Antal beviljade"] + 1)
data__it_fillout["Antal beviljade"] = data__it_fillout["Antal beviljade"].fillna(0)


fig = go.Figure(
    go.Choroplethmapbox(
        geojson=json_data_municipality,
        locations=data__it_fillout["Geo_id"],
        z=data_it_approved,
        featureidkey="properties.id",
        colorscale=[
            [0, "white"],
            [0.00001, "white"],
            [0.05, "lightblue"],
            [0.3, "blue"],
            [1, "darkblue"],
        ],
        marker_opacity=0.9,
        marker_line_width=0.4,
        text=data__it_fillout["Kommun"],
        customdata=data__it_fillout["Antal beviljade"],
        hovertemplate="<b>%{text}</b><br>Beviljade utbildningar <br>DATA/IT: %{customdata}<extra></extra>",
        showscale=False,
    )
)


fig.update_layout(
    title=dict(
        text=f"""
        <b>Antal beviljade DATA/IT</b>
        <br>inom YH i Sverige för
        <br>omgång 2024. Ju mörkare
        <br>blå färg, desto fler
        <br>beviljade utbildningar
        <br>för Data/IT
        <br>för varje kommun
        """,
        x=0.06,
        y=0.75,
        font=dict(size=13),
    ),
    mapbox=dict(style="white-bg", zoom=3.2, center=dict(lat=62, lon=15)),
    width=470,
    height=500,
    margin=dict(r=0, t=50, l=0, b=0),
)


fig.show()
fig.write_html("interactive_figures/approved_data_it_municipality.html")

C:\Users\Marcus\AppData\Local\Temp\ipykernel_6776\1809727718.py:6: DeprecationWarning:

*choroplethmapbox* is deprecated! Use *choroplethmap* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/



In [901]:
df_education_areas[df_education_areas["Utbildningsområde"] == "Data/IT"]

Utbildningsområde          Kommun  Antal beviljade
4            Data/IT       Stockholm               11
10           Data/IT  Flera kommuner                7
12           Data/IT        Göteborg                6
13           Data/IT           Malmö                6
18           Data/IT           Solna                4
30           Data/IT         Mölndal                2
57           Data/IT         Värnamo                1
58           Data/IT           Växjö                1
59           Data/IT          Örebro                1
60           Data/IT           Borås                1
61           Data/IT       Jönköping                1
64           Data/IT     Trollhättan                1